In [1]:
import numpy as np
import pandas as pd
import plotly.express as px

from src.config import ITR_DATA_DIR
from src.utils import get_weight_df
from src.features import transform_density
from src.eval import eval_skill
from src.viz import set_minimal_theme_as_default
set_minimal_theme_as_default()

EXP_NAME = "lag3det_final"

This notebook includes:

* Distribution of target variable
* Model performance summary from OOF prediction (satellite CV and temporal CV)
* Forecasts during October 2003 geomagnetic storms

Please note that atmospheric density unit is in 10^-13 scale

In [2]:
df_gt = pd.read_feather(ITR_DATA_DIR / "sat_density.feather")
df_gt = df_gt.sort_values(["file_id", "timestamp"])
df_gt = transform_density(df_gt)
df_gt = get_weight_df(df_gt)

In [3]:
df_pred_ratio = pd.read_feather(f"runs/{EXP_NAME}/raw_ratio/pred_vf.feather")
df_pred_ratio_log = pd.read_feather(f"runs/{EXP_NAME}/raw_ratio_log/pred_vf.feather")
df_pred_ens = pd.concat([df_pred_ratio, df_pred_ratio_log]).groupby(list(df_pred_ratio.drop(columns=['orbit_mean_density', 'pred_orbit_mean_density'])), as_index=False, dropna=False).mean()

df_pred_ratio = pd.merge(df_pred_ratio, df_gt.reset_index().drop(columns='orbit_mean_density'))
df_pred_ratio_log = pd.merge(df_pred_ratio_log, df_gt.reset_index().drop(columns='orbit_mean_density'))
df_pred_ens = pd.merge(df_pred_ens, df_gt.reset_index().drop(columns='orbit_mean_density'))

df_pred_ratio = df_pred_ratio.assign(is_future=lambda x: x["gfold"] != x["gfold_iter"])
df_pred_ratio_log = df_pred_ratio_log.assign(is_future=lambda x: x["gfold"] != x["gfold_iter"])
df_pred_ens = df_pred_ens.assign(is_future=lambda x: x["gfold"] != x["gfold_iter"])

In [4]:
df_pred_all = pd.concat([
    df_pred_ratio.assign(variant="ratio"),
    df_pred_ratio_log.assign(variant="ratio_log"),
    df_pred_ens.assign(variant="ensemble"),
])

## Target transformation

In [5]:
df_gt_tf = df_pred_ens.sample(n=100000, random_state=42).query('is_future==False').assign(
    satellite_id = lambda x: x["file_prefix"].str.replace("_", ""),
    raw = lambda x: x["orbit_mean_density"],
    ratio = lambda x: x["orbit_mean_density"] / x["msis_density"],
    ratio_log = lambda x: np.log1p(x["ratio"])
)[["satellite_id", "raw", "ratio", "ratio_log"]]

fig_raw = px.histogram(
    df_gt_tf,
    x="raw",
    color="satellite_id"
)
fig_raw.show()

fig_ratio = px.histogram(
    df_gt_tf,
    x="ratio",
    color="satellite_id"
)
fig_ratio.show()

fig_ratio_log = px.histogram(
    df_gt_tf,
    x="ratio_log",
    color="satellite_id"
)
fig_ratio_log.show()

## Model performance

### Satellite CV

In [6]:
eval_skill(df_pred_all.query('is_future==False'), ["variant", "file_prefix"])[[
    "n_records", "wrmse_pred", "wrmse_msis", "skill"
]]

n_records  wrmse_pred  wrmse_msis     skill
variant   file_prefix                                             
ensemble  champ_          952379   10.325477   17.791199  0.419630
          grace1           49459    2.098090    5.160545  0.593436
          grace2         1234839    2.062634    4.045387  0.490127
          grof1           553255    0.383679    0.452583  0.152245
          swarma          614833    1.627272    2.621533  0.379267
ratio     champ_          952379   11.376737   17.791199  0.360541
          grace1           49459    2.082075    5.160545  0.596540
          grace2         1234839    2.035317    4.045387  0.496880
          grof1           553255    0.402192    0.452583  0.111341
          swarma          614833    1.749967    2.621533  0.332464
ratio_log champ_          952379    9.629859   17.791199  0.458729
          grace1           49459    2.222723    5.160545  0.569285
          grace2         1234839    2.185972    4.045387  0.459638
          grof1           553255    0.370306    0.452583  0.181794
          swarma          614833    1.552925    2.621533  0.407627

### Temporal CV

In [7]:
eval_skill(df_pred_all.query('is_future==True'), ["variant", "file_prefix"])[[
    "n_records", "wrmse_pred", "wrmse_msis", "skill"
]]

n_records  wrmse_pred  wrmse_msis     skill
variant   file_prefix                                             
ensemble  champ_          180984   12.661361   54.343188  0.767011
          grace1           51183    3.304045    8.423736  0.607770
          grace2          173604    4.640870    9.851776  0.528931
          grof1           743646    0.172601    0.471759  0.634134
          swarma          306207    0.385009    1.615341  0.761654
ratio     champ_          180984   14.799487   54.343188  0.727666
          grace1           51183    3.641220    8.423736  0.567743
          grace2          173604    4.593693    9.851776  0.533719
          grof1           743646    0.190228    0.471759  0.596768
          swarma          306207    0.413175    1.615341  0.744218
ratio_log champ_          180984   11.896931   54.343188  0.781078
          grace1           51183    3.185157    8.423736  0.621883
          grace2          173604    4.768223    9.851776  0.516004
          grof1           743646    0.166866    0.471759  0.646289
          swarma          306207    0.369880    1.615341  0.771021

### Horizon error

In [8]:
smr_hrz = pd.concat([
    df_pred_ens.assign(
        pred_orbit_mean_density=lambda x: x['msis_density'],
        method='msis'
    ),
    df_pred_ens.assign(method='ensemble')
]).assign(
    sqe = lambda x: (x['orbit_mean_density'] - x['pred_orbit_mean_density'])**2,
).groupby(['method', 'horizon', 'is_future']).agg(
    n_records = ('sqe', 'size'),
    mse = ('sqe', 'mean'),
).assign(
    rmse = lambda x: np.sqrt(x['mse']),
)

px.line(
    smr_hrz.reset_index().query('horizon <= 432 & is_future==False'),
    x='horizon',
    y='rmse',
    color='method'
)

In [9]:
smr_hrz_sat = pd.concat([
    df_pred_ens.assign(
        pred_orbit_mean_density=lambda x: x['msis_density'],
        method='msis'
    ),
    df_pred_ens.assign(method='ensemble')
]).assign(
    sqe = lambda x: (x['orbit_mean_density'] - x['pred_orbit_mean_density'])**2,
).groupby(['file_prefix', 'method', 'horizon', 'is_future']).agg(
    n_records = ('sqe', 'size'),
    mse = ('sqe', 'mean'),
).assign(
    rmse = lambda x: np.sqrt(x['mse']),
)

px.line(
    smr_hrz_sat.reset_index().query('horizon <= 432 & is_future==False').assign(
        file_prefix = lambda x: x['file_prefix'].str.replace("_", "")
    ),
    x='horizon',
    y='rmse',
    color='method',
    facet_col='file_prefix',
    facet_col_wrap=3
).update_yaxes(matches=None).for_each_annotation(lambda a: a.update(text=a.text.split('=')[-1]))

## Forecasts - 2003 Halloween Solar Storms

In [10]:
fig = px.line(
    df_pred_ens.query('file_id >= "00748" & file_id <= "00750" & is_future==False').assign(
        pred_orbit_mean_density = lambda x: np.where(x['file_id'] < "00749", np.NaN, x['pred_orbit_mean_density']),
        msis_density = lambda x: np.where(x['file_id'] < "00749", np.NaN, x['msis_density'])
    ),
    x='timestamp',
    y=['orbit_mean_density', 'pred_orbit_mean_density', 'msis_density'],
    line_group='file_id',
).update_layout(
    xaxis_title="Timestamp",
    yaxis_title="Atmospheric Density (10⁻¹³ kg/m³)",
    legend_title_text=None,
    margin=dict(l=10, r=10, t=0, b=10)
)
fig.write_image("reports/images/plot/forecast-champ-oct-2003.png", width=800, height=400, scale=2)
fig